# Simulation #1
This workbook is a first attempt at constructing a simulation of a stochastic dynamical system, with an accompanying estimation of the Perron-Frobenius operator.

In [92]:
using LinearAlgebra, Plots, Distributions

In [93]:
plotly();

In [94]:
function generate_grid(min::Number, max::Number, resolution::Int64)
    xs = LinRange(min, max, resolution);
    ys = LinRange(min, max, resolution);
    grid = [[x, y] for x in xs for y in ys];
    grid = transpose(hcat(grid...));
    grid = convert(Array{Float64}, grid);
    return grid
end;

## Setting up the dynamics
The state space $X$ of our dynamical system will be the flat torus $\mathbb{T}^2$, represented by the unit square.

In [95]:
range = 2π;
grid_size = 100;
n_gridpoints = grid_size ^ 2;

In [96]:
grid = generate_grid(0, range, grid_size);

We will define an initial density $f_0 (x, y)$ on this state space.

In [122]:
function f₀(x, simple)
    if simple
        d = MvNormal([π, π], 1)
        return pdf(d, x)
    else
        M = [π/2 π/2; 3π/2 π/2; π/2 3π/2; 3π/2 3π/2]
        σ = 1
        Σ = σ .* [1 0; 0 1]
        weights = 1 / 4
        value = 0
        for i in 1:4
            d = MvNormal(M[i,:], Σ)
            eval = pdf(d, x)
            value += weights * eval
        end
    end
    return value
end;

In [123]:
f0s = [f₀(grid[n,:], true) for n in 1:n_gridpoints]
scatter(grid[:,1], grid[:,2], f0s, markersize=1)

<!DOCTYPE html>
 
 
 Plots.jl

To obtain a sample from this initial density $f_0$, we can use rejection sampling.

In [139]:
n_samples = 10000
candidate_points = 2π .* rand(n_samples,2)
f0s = [f₀(candidate_points[n,:], true) for n in 1:n_samples]
thresholds = 1/40 .* rand(n_samples)
sample = candidate_points[f0s .> thresholds, :]

histogram2d(sample[:,1], sample[:,2], bins=30)

<!DOCTYPE html>
 
 
 Plots.jl

In [140]:
sample_size = size(sample, 1);
print("We obtain an initial sample of $sample_size points")

We obtain an initial sample of 4520 points

The particular map $S: \mathbb{T}^2 \to \mathbb{T}^2$ we choose to introduce the dynamics is the standard map, given by
$$
S ([x , y]) := \begin{bmatrix} x + y \\ y + a \sin ( x + y) \end{bmatrix} \mod 1
$$
where $a$ is a parameter which for the moment we take to be $a=6$. This map is easily wrapped in a function which can then be iterated forward across timesteps.

In [141]:
function S(x)
    a = 6;
    result = [x[:,1]+x[:,2] x[:,2] + a*sin.(x[:,1]+x[:,2])];
    result = mod.(result,2π)
    return result
end;

function S_forward(x, n_steps::Int64)
    for t in 1:n_steps
        x = S(x)
    end
    return x
end;

We can then easily compare the initial density $f_0$ with a naive estimate of a limiting density $f_*$ by computing the latter with a big value for ```S_forward```.

In [142]:
fstar = S_forward(sample, 100);

In [144]:
histogram2d(fstar[:,1], fstar[:,2], bins=30)

<!DOCTYPE html>
 
 
 Plots.jl

This map $S$ is volume preserving, so we should expect to see the same density no matter how many times $S$ is applied.

## Estimating the Perron-Frobenius operator
Having established a model for the dynamics, next we want to estimate the Perron-Frobenius operator. 
$$
\mathcal{P} : L^1(X) \to L^1(X)
$$
Actually we will be estimating a stochastically perturbed version of $\mathcal{P}$, described by
$$
 \mathcal{L} f(y) = \int_X k(Sx, y ) f(x) dx
$$
where $k(x, y) = \phi(x-y)$.

To estimate $\mathcal{L}$, we first must define a finite basis for $L^1(X)$. For the moment we will take this basis to be a uniform grid of radial basis functions (RBFs) $\varphi_i$. These will be of the form
$$
\varphi_i (x) = \phi ( x - z_i ) := \exp \left( - \frac{\| x - z_i \|^2}{\epsilon^2} \right)
$$
where the $z_i$ denote the centres of each RBF and $\epsilon$ is some bandwidth parameter.

In [13]:
φ(x, z, ϵ) =  exp( -1 * ( norm(x - z) / ϵ ) ^ 2 );

In [81]:
ϵ = 1;
c = π * ϵ^2;

In [145]:
basis_grid_size = 25;
n_bases = basis_grid_size ^ 2;

print("We construct a basis of $n_bases RBFs")

We construct a basis of 625 RBFs

In [16]:
basis_locs = generate_grid(0, 2π, basis_grid_size);

These basis functions can be easily visualised by evaluating all grid points against each.

In [17]:
evaluation_matrix = zeros(n_gridpoints, n_bases)
for b in 1:n_bases
    for i in 1:n_gridpoints
        evaluation_matrix[i, b] = φ(grid[i, :], basis_locs[b, :], ϵ)
    end
end

In [18]:
scatter(grid[:,1], grid[:,2], evaluation_matrix[:,270], markersize=1, label="Basis #270")
scatter!(grid[:,1], grid[:,2], evaluation_matrix[:,567], markersize=1, label="Basis #567")

<!DOCTYPE html>
 
 
 Plots.jl

In order to estimate the integral
$$
    \mathcal{L} f(y) = \int_X k (Sx, y) f(x) dx
$$
we will also need an approximate Lebesgue measure for the integral wrt $dx$. This will be some weighted combination of all the datapoints, subject to the constraint that obviously each basis function integrates to a constant. This requires computing an evaluation matrix $\Phi$ of all sample points against all basis functions.

In [19]:
Φ = zeros(n_bases, sample_size)
for b in 1:n_bases
    for n in 1:sample_size
        evaluation = φ(sample[n, :], basis_locs[b,:], ϵ)
        Φ[b, n] = evaluation
    end
end

Having done so, we can then estimate the weights $w$ using nonnegative least squares.

In [20]:
C = c * ones(n_bases);

In [21]:
include("nnlsq.jl");

In [22]:
w, residual, objvalue = nnlsq(Φ, C, 0);

Academic license - for non-commercial use only - expires 2021-08-05
Warning for adding constraints: zero or small (< 1e-13) coefficients, ignored
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (mac64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 625 rows, 5132 columns and 2585071 nonzeros
Model fingerprint: 0x1784ea93
Model has 625 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e-13, 1e+00]
  Objective range  [0e+00, 0e+00]
  QObjective range [2e+00, 2e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+00, 3e+00]
Presolve time: 0.62s
Presolved: 625 rows, 5132 columns, 2585071 nonzeros
Presolved model has 625 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 1.950e+05
 Factor NZ  : 1.956e+05 (roughly 4 MBytes of memory)
 Factor Ops : 8.158e+07 (less than 1 second per iteration)
 Threads    : 2

                  Objective                Residual
Iter       Primal      

With these weights, we can now write the image of any basis function $\varphi_i$ under $\mathcal{L}$ as a linear combination of kernels centered at the image points, denoted $\varphi_{y_j}$. But we obviously want to be able to write $\mathcal \varphi_i$ as just a linear combination of the $\varphi_i$. To do this, we will need to write each $\varphi_{y_j}$ itself as a linear combination of the $\varphi_i$.
$$
 \varphi_{y_j} (y) = \sum_{i=1}^m \gamma_i \varphi_i (y)
$$
The weights $\gamma_i$ will be calculated as the integrals of $\varphi_{y_j}$ over a Voronoi tesselation of the basis functions $\varphi_i$, scaled according to weights $c_i$.

In [23]:
X = sample;
Y = S(X);

In [72]:
function integrate_phiy(Y, basis_locs)
    # integrates φ at each y_j across a Voronoi tesselation over m basis functions with centres zs
    # returns the m integral values

    fine_grid_size = 100;
    n_fine_gridpoints = fine_grid_size ^ 2;
    fine_grid = generate_grid(0,2π, fine_grid_size)

    distance_matrix = zeros(n_fine_gridpoints, n_bases)

    for g in 1:n_fine_gridpoints
        for b in 1:n_bases
           dist = norm(fine_grid[g,:] - basis_locs[b,:])
           distance_matrix[g,b] = dist
        end
    end

    tile_indexes = argmin(distance_matrix, dims=2);
    tile_indexes = [ind[2] for ind in tile_indexes];
    tile_indexes = tile_indexes[:];
    
    integral_values = zeros(sample_size, n_bases)
    
    for j in 1:sample_size
        y_j = Y[j,:]
        for b in 1:n_bases
            relevant_points = tile_indexes .== b
            Vb = fine_grid[relevant_points,:];
            n_relevant_points = size(Vb, 1)

            evaluation = 0
            for i in 1:n_relevant_points
                evaluation += φ(Vb[i,:], y_j, ϵ)
            end
            result = ((2π)^2 / sample_size) * evaluation
            integral_values[j,b] = result
        end
    end
    return integral_values
end;

In [73]:
Ξ = integrate_phiy(Y, basis_locs);

4507×625 Matrix{Float64}:
 3.21816e-8   2.04021e-7   1.01126e-6   …  1.76513e-13  4.25686e-14
 3.6676e-14   2.03514e-13  8.7462e-13      2.153e-6     4.55116e-7
 3.52886e-11  3.17753e-10  2.28679e-9      5.94036e-11  2.01487e-11
 2.16631e-12  1.27399e-11  5.82709e-11     2.5512e-7    5.71287e-8
 6.50499e-13  4.89655e-12  2.91443e-11     3.53468e-7   1.00837e-7
 3.31995e-13  9.30011e-13  1.90089e-12  …  6.13989e-10  6.46431e-11
 2.20529e-18  4.33706e-18  5.98468e-18     3.17088e-12  2.29474e-13
 1.35868e-18  2.91577e-17  5.20232e-16     1.35973e-11  1.03553e-11
 4.38913e-14  3.04356e-13  1.66004e-12     3.41827e-6   9.00169e-7
 5.53936e-6   1.27325e-5   2.09077e-5      1.11957e-15  9.56987e-17
 8.35232e-18  1.03595e-16  1.04433e-15  …  4.39614e-5   2.02061e-5
 0.00238252   0.00545524   0.00891948      6.28391e-21  5.34936e-22
 2.69207e-25  3.65061e-24  4.04048e-23     0.0261131    0.0130472
 ⋮                                      ⋱               
 9.93618e-20  6.11095e-19  2.9323e-18   

This is now everything we need to compute the matrix $L$.

In [86]:
function estimate_L(w, Φ, Ξ)
    L = zeros(n_bases, n_bases)
    for b in 1:n_bases
        for k in 1:n_bases
            val = 0
            for n in 1:sample_size
                val += w[n] * Φ[b,n] * Ξ[n,k]
            end
            val = 1/C * val
            L[b,k] = val            
        end
    end
    return L
end;

estimate_L (generic function with 1 method)

In [87]:
L = estimate_L(w, Φ, Ξ);

625×625 Matrix{Float64}:
 0.000933199  0.00287114   0.00656428   …  3.48267e-9   1.2202e-9
 0.00101704   0.00305056   0.00683288      1.30461e-8   4.55868e-9
 0.00105156   0.00301879   0.00651036      4.31982e-8   1.50634e-8
 0.0010752    0.00290008   0.00589138      1.27177e-7   4.42518e-8
 0.00111098   0.00279888   0.00527589      3.37035e-7   1.17109e-7
 0.00114141   0.00271782   0.00477281   …  8.2135e-7    2.85989e-7
 0.00112006   0.00257049   0.00428757      1.90139e-6   6.69114e-7
 0.00101033   0.00227133   0.00367376      4.34807e-6   1.56737e-6
 0.000816881  0.00181682   0.00289074      1.01045e-5   3.77657e-6
 0.000583952  0.00129149   0.00203759      2.38145e-5   9.25744e-6
 0.000366631  0.000808207  0.00126934   …  5.52435e-5   2.22175e-5
 0.000201578  0.000443307  0.000694269     0.000121705  5.02886e-5
 9.69581e-5   0.000212745  0.00033242      0.000248654  0.000105278
 ⋮                                      ⋱               
 5.69351e-5   0.000136868  0.000242484     0.00

## Evaluating our estimate
Now we have an estimate of $L$, we can evaluate it.